In [1]:
import numpy as np
import math
import pandas as pd
import geopandas as gpd

import json
import plotly.express as px
import plotly

In [2]:
# https://qiita.com/yuusei/items/549402a80efd7e7192ef
# -*- coding: utf-8 -*-
import math as mt


def grid1st(lon, lat):  # 1次メッシュ(4桁) 分割なし
    return int(mt.floor(lat*1.5)) * 100 + int(mt.floor(lon-100))

def grid2nd(lon, lat):  # 2次メッシュ(6桁) 8分割
    return (int(mt.floor(lat*12       / 8))   * 10000 + int(mt.floor((lon-100)*8         / 8))  * 100   +   
            int(mt.floor(lat*12 %  8     ))   * 10    + int(mt.floor((lon-100)*8))  %  8               )  

def grid3rd(lon, lat):  # 3次メッシュ(8桁) 8分割x10分割=80分割
    return (int(mt.floor(lat*120      / 80)) * 1000000 + int(mt.floor((lon-100))             ) * 10000 +  # 1次メッシュ
            int(mt.floor(lat*120 % 80 / 10)) * 1000    + int(mt.floor((lon-100)*80 % 80 / 10)) * 100 +    # 2次メッシュ
            int(mt.floor(lat*120 % 10))      * 10      + int(mt.floor((lon-100)*80)) % 10               ) 

def grid4th(lon, lat):  # 4次メッシュ(9桁) 8分割x10分割x2分割=160分割
    return (int(mt.floor(lat*240       / 160)) * 10000000 + int(mt.floor((lon-100)*160       / 160)) * 100000 +    # 1次メッシュ
            int(mt.floor(lat*240 % 160 / 20))  * 10000    + int(mt.floor((lon-100)*160 % 160 / 20))  * 1000   +    # 2次メッシュ
            int(mt.floor(lat*240 % 20  / 2))   * 100      + int(mt.floor((lon-100)*160 % 20  / 2))   * 10     +    # 3次メッシュ
            int(mt.floor(lat*240)) % 2         * 2        + int(mt.floor((lon-100)*160)) % 2                  + 1) # 4次メッシュ

if __name__ == "__main__":
    lon = 139.74954 # 虎ノ門ヒルズ
    lat = 35.666863 # 虎ノ門ヒルズ
    print('1次メッシュ： ', grid1st(lon, lat))  # 5339
    print('2次メッシュ： ', grid2nd(lon, lat))  # 533945
    print('基準地域メッシュ： ', grid3rd(lon, lat))  # 53394509
    print('4次メッシュ： ', grid4th(lon, lat))  # 533945092

1次メッシュ：  5339
2次メッシュ：  533945
基準地域メッシュ：  53394509
4次メッシュ：  533945092


In [3]:
url = "https://www.sinfonica.or.jp/kanko/estrela/refer/s29/tokyo3.csv"
df = pd.read_csv(url, header=None, encoding="shift-jis")
#df = pd.read_csv("tokyo3.csv", header=None)

df.columns = ["name", "address", "lon", "lat"]
df["lon"] = df["lon"].astype(float)
df["lat"] = df["lat"].astype(float)

df["tag"] = df["name"].str[0:4]
rank9 = df["tag"].value_counts()[0:9].index
df["tag"].where(df["tag"].isin(rank9), "他", inplace=True)

df["mesh_cd"] = df.apply(lambda f: grid3rd(f["lon"], f["lat"]), axis=1)
df

name              address         lon        lat   tag  \
0      セブンイレブン日本橋大伝馬町店        東京都中央区大伝馬町1-7  139.772572  35.671400  セブンイ   
1         ジェイ・ショップ五日市店        東京都あきる野市舘谷287  139.232762  35.729356     他   
2        セブンイレブン稲城大丸東店        東京都稲城市大丸642-1  139.499690  35.641551  セブンイ   
3         サンクス昭島中神町新畑店  東京都昭島市中神町字中新畑1157-5  139.382917  35.717136  サンクス   
4        セブンイレブン奥多摩古里店     東京都西多摩郡奥多摩町小丹波33  139.151941  35.815525  セブンイ   
...                ...                  ...         ...        ...   ...   
5495     セブンイレブン練馬3丁目店       東京都練馬区練馬3−1−10  139.650390  35.737360  セブンイ   
5496  ローソンストア１００練馬３丁目店        東京都練馬区練馬3-1-7  139.650390  35.737360  ローソン   
5497        ミニストップ豊島園店      東京都練馬区練馬3-24-18  139.648470  35.739040  ミニスト   
5498     セブンイレブン豊島園駅前店      東京都練馬区練馬4-15-17  139.648450  35.742770  セブンイ   
5499    ファミリーマート豊島園駅前店       東京都練馬区練馬4-17-2  139.647640  35.742680  ファミリ   

       mesh_cd  
0     53394601  
1     53394178  
2     53393369  
3     53394360  
4     53395172  
...        ...  
5495  53394582  
5496  53394582  
5497  53394581  
5498  53394591  
5499  53394591  

[5500 rows x 6 columns]

In [4]:
df2 = pd.pivot_table(
    df.groupby(["mesh_cd", "tag"], as_index=False).size(),
    index="mesh_cd", columns="tag", values=df.groupby(["mesh_cd", "tag"], as_index=False).size(), fill_value=0
)
df2.columns = ["エーエム", "サンクス", "サークル", "スリーエ", "セブンイ", "デイリー", "ファミリ", "ミニスト", "ローソン", "他"]
df2.reset_index(inplace=True)
df2["idxmax"] = df2.iloc[:, 1:].idxmax(axis=1)
df2

mesh_cd  エーエム  サンクス  サークル  スリーエ  セブンイ  デイリー  ファミリ  ミニスト  ローソン  他 idxmax
0     53392317     2     1     1     0     1     0     0     0     0  0   エーエム
1     53392318     0     0     0     0     1     0     0     0     0  0   セブンイ
2     53392327     0     1     0     2     0     0     0     1     0  0   スリーエ
3     53392328     1     0     0     0     0     0     0     0     0  0   エーエム
4     53392336     0     0     0     1     1     0     1     0     0  0   スリーエ
...        ...   ...   ...   ...   ...   ...   ...   ...   ...   ... ..    ...
1030  53395670     0     0     0     0     1     0     0     0     0  0   セブンイ
1031  53395671     0     0     0     1     1     0     2     0     0  2   ファミリ
1032  53395675     0     0     0     0     1     0     0     0     0  0   セブンイ
1033  53395700     0     0     0     0     2     0     0     0     0  0   セブンイ
1034  53395730     0     1     0     0     1     0     0     0     0  0   サンクス

[1035 rows x 12 columns]

In [5]:
df3 = gpd.read_file("https://www.geospatial.jp/ckan/dataset/ee0203ee-d526-419c-b894-950b03a1ecd0/resource/9f93ab0c-a157-4408-b492-41c1e036eaac/download/13tokyo1km.geojson")
#df3 = gpd.read_file("13tokyo1km.geojson")

df3.rename(columns={"code":"mesh_cd"}, inplace=True)
df3["mesh_cd"] = df3["mesh_cd"].astype(int)
df3 = df3.merge(df2[["mesh_cd", "idxmax"]], on="mesh_cd",how="right")
df3.to_csv("conbini_tokyo.csv")
df3

mesh_cd                                           geometry idxmax
0     53392317  POLYGON ((139.46250 35.50833, 139.47500 35.508...   エーエム
1     53392318  POLYGON ((139.47500 35.50833, 139.48750 35.508...   セブンイ
2     53392327  POLYGON ((139.46250 35.51667, 139.47500 35.516...   スリーエ
3     53392328  POLYGON ((139.47500 35.51667, 139.48750 35.516...   エーエム
4     53392336  POLYGON ((139.45000 35.52500, 139.46250 35.525...   スリーエ
...        ...                                                ...    ...
1030  53395670  POLYGON ((139.75000 35.80833, 139.76250 35.808...   セブンイ
1031  53395671  POLYGON ((139.76250 35.80833, 139.77500 35.808...   ファミリ
1032  53395675  POLYGON ((139.81250 35.80833, 139.82500 35.808...   セブンイ
1033  53395700  POLYGON ((139.87500 35.75000, 139.88750 35.750...   セブンイ
1034  53395730  POLYGON ((139.87500 35.77500, 139.88750 35.775...   サンクス

[1035 rows x 3 columns]

In [6]:
c = plotly.colors.qualitative.Plotly

fig = px.choropleth_mapbox(
    df3,
    geojson = json.loads(df3.set_index("mesh_cd")[["geometry"]].to_json()),
    locations = df3["mesh_cd"],
    color = df3["idxmax"],
    color_discrete_sequence = c,
    #category_orders = {"cluster":["0", "1", "2", "3", "4", "5", "6"]},
    opacity = 0.5,
    center = {'lat':35.7, 'lon':139.45},
    mapbox_style = "open-street-map",
    height = 600,
    width = 1000,
    zoom = 9.1
)

fig.update_layout(margin=dict(t=10, b=10, l=20, r=20))
fig.show()